In [1]:
import numpy as np
import h5py
import glob
from pycbc import conversions
from pycbc import coordinates

In [2]:
path = ['/work/yifan.wang/4ogc/release_prod/convertsnr/1212_posterior/']
posfile = []
for p in path:
    f = glob.glob(p+'/*.hdf')
    posfile.extend(f)

In [3]:
posfile

['/work/yifan.wang/4ogc/release_prod/convertsnr/1212_posterior/GW190513_205428-PYCBC-POSTERIOR-IMRPhenomXPHM.hdf',
 '/work/yifan.wang/4ogc/release_prod/convertsnr/1212_posterior/GW190421_213856-PYCBC-POSTERIOR-IMRPhenomXPHM.hdf',
 '/work/yifan.wang/4ogc/release_prod/convertsnr/1212_posterior/GW190425_081805-PYCBC-POSTERIOR-IMRPhenomXPHM.hdf',
 '/work/yifan.wang/4ogc/release_prod/convertsnr/1212_posterior/GW190630_185205-PYCBC-POSTERIOR-IMRPhenomXPHM.hdf',
 '/work/yifan.wang/4ogc/release_prod/convertsnr/1212_posterior/GW190519_153544-PYCBC-POSTERIOR-IMRPhenomXPHM.hdf',
 '/work/yifan.wang/4ogc/release_prod/convertsnr/1212_posterior/GW191230_180458-PYCBC-POSTERIOR-IMRPhenomXPHM.hdf',
 '/work/yifan.wang/4ogc/release_prod/convertsnr/1212_posterior/GW200208_130117-PYCBC-POSTERIOR-IMRPhenomXPHM.hdf',
 '/work/yifan.wang/4ogc/release_prod/convertsnr/1212_posterior/GW191204_171526-PYCBC-POSTERIOR-IMRPhenomXPHM.hdf',
 '/work/yifan.wang/4ogc/release_prod/convertsnr/1212_posterior/GW170608_020116-P

In [4]:
s = np.size(posfile)

In [5]:
s

94

In [6]:
def extract_quantile(sample):
    '''
    Given a sample, this function output the median+x-y
    '''
    return np.quantile(sample,0.5), np.quantile(sample,0.95) -np.quantile(sample,0.5),\
            np.quantile(sample,0.5) - np.quantile(sample,0.05)

In [7]:
m1 = np.zeros((s,3))
m2 = np.zeros((s,3))
mc = np.zeros((s,3))
q = np.zeros((s,3))
chi = np.zeros((s,3))
dist = np.zeros((s,3))
z = np.zeros((s,3))
labels = []
mf = np.zeros((s,3))
chif = np.zeros((s,3))
snr = np.zeros(s)
detm1 = np.zeros((s,3))
detm2 = np.zeros((s,3))
detmc = np.zeros((s,3))
detmf = np.zeros((s,3))

In [8]:
labels

[]

In [10]:
for i,path in enumerate(posfile):
    f = h5py.File(path,'r')
    #name
    name = 'GW'+path.split('GW')[1][:6]+r'_'+path.split('GW')[1][7:13]
    
    if name == 'GW170817_124104' or name =='GW190425_081805' or name == 'GW200105_162426' or name == 'GW200115_042309':
        m1[i][0],m1[i][1],m1[i][2] = extract_quantile(f['samples']['srcmass1']) 
        m2[i][0],m2[i][1],m2[i][2] = extract_quantile(f['samples']['srcmass2'])
        mc[i][0],mc[i][1],mc[i][2] = extract_quantile(f['samples']['srcmchirp'])
        q[i][0],q[i][1],q[i][2] = extract_quantile(f['samples']['q'])
        chi[i][0],chi[i][1],chi[i][2] = extract_quantile(f['samples']['chi_eff'])
        dist[i][0],dist[i][1],dist[i][2] = extract_quantile(f['samples']['distance'])
        z[i][0],z[i][1],z[i][2] = extract_quantile(f['samples']['redshift'])
        snr[i] = np.max(conversions.snr_from_loglr(f['samples']['loglr'][:]))
        labels.append(name)
        mf[i][0],mf[i][1],mf[i][2] = np.nan,np.nan,np.nan
        chif[i][0],chif[i][1],chif[i][2] = np.nan,np.nan,np.nan
        detm1[i][0],detm1[i][1],detm1[i][2]=extract_quantile(f['samples']['srcmass1'][:]*(1+f['samples']['redshift'][:]))
        detm2[i][0],detm2[i][1],detm2[i][2]=extract_quantile(f['samples']['srcmass2'][:]*(1+f['samples']['redshift'][:]))
        detmc[i][0],detmc[i][1],detmc[i][2]=extract_quantile(f['samples']['srcmchirp'][:]*(1+f['samples']['redshift'][:]))
        detmf[i][0],detmf[i][1],detmf[i][2]=np.nan,np.nan,np.nan

    else:
        m1[i][0],m1[i][1],m1[i][2] = extract_quantile(f['samples']['srcmass1']) 
        m2[i][0],m2[i][1],m2[i][2] = extract_quantile(f['samples']['srcmass2'])
        mc[i][0],mc[i][1],mc[i][2] = extract_quantile(f['samples']['srcmchirp'])
        q[i][0],q[i][1],q[i][2] = extract_quantile(f['samples']['q'])
        chi[i][0],chi[i][1],chi[i][2] = extract_quantile(f['samples']['chi_eff'])
        dist[i][0],dist[i][1],dist[i][2] = extract_quantile(f['samples']['distance'])
        z[i][0],z[i][1],z[i][2] = extract_quantile(f['samples']['redshift'])
        snr[i] = np.max(conversions.snr_from_loglr(f['samples']['maxl_loglr'][:]))
        labels.append(name)
    #Cartesian spin
        spin1_x,spin1_y,spin1_z = coordinates.spherical_to_cartesian(f['samples']['spin1_a'], \
                                                              f['samples']['spin1_azimuthal'],\
                                                              f['samples']['spin1_polar'])
        spin2_x,spin2_y,spin2_z = coordinates.spherical_to_cartesian(f['samples']['spin2_a'], \
                                                              f['samples']['spin2_azimuthal'],\
                                                              f['samples']['spin2_polar'])
    # final mass
        mfsample = conversions.final_mass_from_initial(mass1=f['samples']['srcmass1'],\
                                                   mass2=f['samples']['srcmass2'],\
                                                   spin1x=spin1_x,spin1y=spin1_y,spin1z=spin1_z,\
                                                   spin2x=spin2_x,spin2y=spin2_y,spin2z=spin2_z,\
                                                   )
        mf[i][0],mf[i][1],mf[i][2] = extract_quantile(mfsample)
    #final spin
        chifsample = conversions.final_spin_from_initial(mass1=f['samples']['srcmass1'],\
                                                   mass2=f['samples']['srcmass2'],\
                                                   spin1x=spin1_x,spin1y=spin1_y,spin1z=spin1_z,\
                                                   spin2x=spin2_x,spin2y=spin2_y,spin2z=spin2_z,\
                                                   )
        chif[i][0],chif[i][1],chif[i][2] = extract_quantile(chifsample)
        detm1[i][0],detm1[i][1],detm1[i][2]=extract_quantile(f['samples']['srcmass1'][:]*(1+f['samples']['redshift'][:]))
        detm2[i][0],detm2[i][1],detm2[i][2]=extract_quantile(f['samples']['srcmass2'][:]*(1+f['samples']['redshift'][:]))
        detmc[i][0],detmc[i][1],detmc[i][2]=extract_quantile(f['samples']['srcmchirp'][:]*(1+f['samples']['redshift'][:]))
        detmf[i][0],detmf[i][1],detmf[i][2]=extract_quantile(mfsample*(1+f['samples']['redshift'][:]))
        
    f.close()

In [11]:
labels

['GW190513_205428',
 'GW190421_213856',
 'GW190425_081805',
 'GW190630_185205',
 'GW190519_153544',
 'GW191230_180458',
 'GW200208_130117',
 'GW191204_171526',
 'GW170608_020116',
 'GW190413_052954',
 'GW190527_092055',
 'GW170809_082821',
 'GW200216_220804',
 'GW151226_033853',
 'GW190707_093326',
 'GW190731_140936',
 'GW170202_135657',
 'GW191109_010717',
 'GW191129_134029',
 'GW170304_163753',
 'GW191105_143521',
 'GW200219_094415',
 'GW190828_063405',
 'GW190910_112807',
 'GW200302_015811',
 'GW200106_134123',
 'GW200214_223307',
 'GW170104_101158',
 'GW170121_212536',
 'GW200129_114245',
 'GW200316_215756',
 'GW170823_131358',
 'GW190412_053044',
 'GW190602_175927',
 'GW170818_022509',
 'GW150914_095045',
 'GW190408_181802',
 'GW190521_030229',
 'GW191204_110529',
 'GW200202_154313',
 'GW191126_115259',
 'GW200306_093714',
 'GW190925_232845',
 'GW200225_060421',
 'GW200311_115853',
 'GW190814_211039',
 'GW191215_223052',
 'GW190514_065416',
 'GW200210_005122',
 'GW170727_010430',


In [12]:
header = 'event \t srcmass1 \t srcmass1_plus \t srcmass1_minus \t srcmass2 \t srcmass2_plus \t srcmass2_minus \t '+\
'srcmchirp \t srcmchirp_plus \t srcmchirp_minus \t q \t q_plus \t q_minus \t chi_eff \t chi_eff_plus \t chi_eff_minus \t '+\
'distance \t distance_plus \t distance_minus \t redshift \t redshift_plus \t redshift_minus \t '+\
'remnantmass \t remnantmass_plus \t remnantmass_minus \t remnantspin \t remnantspin_plus \t remnantspin_minus \t snr \t '+\
'detmass1 \t detmass1_plus \t detmass1_minus \t detmass2 \t detmass2_plus \t detmass2_minus \t detmchirp \t '+\
'detmchirp_plus \t detmchirp_minus \t detremnantmass \t detremnantmass_plus \t detremnantmass_minus'

In [13]:
np.savetxt('PEtable.txt',np.transpose([labels,m1[:,0],m1[:,1],m1[:,2],\
                                       m2[:,0],m2[:,1],m2[:,2],\
                                      mc[:,0],mc[:,1],mc[:,2],\
                                      q[:,0],q[:,1],q[:,2],\
                                      chi[:,0],chi[:,1],chi[:,2],\
                                      dist[:,0],dist[:,1],dist[:,2],\
                                      z[:,0],z[:,1],z[:,2],\
                                      mf[:,0],mf[:,1],mf[:,2],\
                                      chif[:,0],chif[:,1],chif[:,2],\
                                      snr,\
                                      detm1[:,0],detm1[:,1],detm1[:,2],\
                                      detm2[:,0],detm2[:,1],detm2[:,2],\
                                      detmc[:,0],detmc[:,1],detmc[:,2],\
                                      detmf[:,0],detmf[:,1],detmf[:,2]]),fmt='%s',delimiter=',',header=header)